# 509 Final Project

## Rsolve dependencies

## Globally import libraries

In [1]:
import numpy as np
import pandas as pd
import pymysql as mysql
import matplotlib.pyplot as plt
import os
import shutil
import re
import logging
import time
import zipfile
import requests
from bs4 import BeautifulSoup
import datetime
import re
import regex as rex
from collections import defaultdict, Counter
import random
#import mysql.connector

# Set pandas global options
pd.options.display.max_rows = 17

## Initiate MySQL connection

In [2]:
'''Set local environment variables to hide user name & password citation:
https://www.geeksforgeeks.org/how-to-hide-sensitive-credentials-using-python/'''

user_name = os.environ['MySQLUSRAC']
user_pass = os.environ['MySQLPWDAC']

# Instantiate connection
db_conn = mysql.connect(host='localhost',
                        port=int(3306),
                        user=user_name,
                        passwd=user_pass,
                        db='509_final_proj')

# Create a cursor object
cursor = db_conn.cursor()

In [3]:
tbl_names = pd.read_sql('SHOW TABLES', db_conn)

display(tbl_names)
print(type(tbl_names))

C:\Users\acarr\AppData\Local\Temp\ipykernel_40760\4193860975.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  tbl_names = pd.read_sql('SHOW TABLES', db_conn)


Tables_in_509_final_proj
0                 nar_temp
1            news_articles

<class 'pandas.core.frame.DataFrame'>


## Read URLs from MySQL table to perform web scraping

In [4]:
'''Set local environment variables to hide user name & password citation:
https://www.geeksforgeeks.org/how-to-hide-sensitive-credentials-using-python/'''

user_name = os.environ['MySQLUSRAC']
user_pass = os.environ['MySQLPWDAC']

# Instantiate connection
db_conn = mysql.connect(host='localhost',
                        port=int(3306),
                        user=user_name,
                        passwd=user_pass,
                        db='509_final_proj')

# Create a cursor object
cursor = db_conn.cursor()

In [5]:
nat_tbl_name = 'nar_temp'
nwa_tbl_name = 'news_articles'

In [6]:
text_query = f"SELECT url, article_text FROM {nwa_tbl_name}"
df = pd.read_sql(text_query, db_conn)

C:\Users\acarr\AppData\Local\Temp\ipykernel_40760\2936052196.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql(text_query, db_conn)


In [7]:
print(df.head())
story_str000 = df['article_text'][0]
print(story_str000)

                                                 url  \
0  https://www.cnn.com/2023/06/01/politics/senate...   
1  https://www.foxnews.com/politics/pro-scott-sup...   
2  https://www.foxnews.com/us/pennsylvania-bus-dr...   
3  https://www.foxnews.com/us/bob-lee-murder-cash...   
4  https://www.foxnews.com/politics/senate-gop-de...   

                                        article_text  
0  <!DOCTYPE html>\n<html data-layout-uri="cms.cn...  
1  <!DOCTYPE html>\n<html data-n-head="%7B%22lang...  
2  <!DOCTYPE html>\n<html data-n-head="%7B%22lang...  
3  <!DOCTYPE html>\n<html data-n-head="%7B%22lang...  
4  <!DOCTYPE html>\n<html data-n-head="%7B%22lang...  
<!DOCTYPE html>
<html data-layout-uri="cms.cnn.com/_layouts/layout-with-rail/instances/politics-article-v1@published" data-uri="cms.cnn.com/_pages/h_c65f588d1ba1a13ef5d11b7028741326@published" lang="en">
 <head>
  <style>
   body,h1,h2,h3,h4,h5{font-family:'CNN Sans Display',Helvetica Neue,Helvetica,Arial,Utkal,sans-serif}@font-fac

In [8]:
story_str000_bs = BeautifulSoup(story_str000, 'html.parser')
rex_art = rex.compile(r'articleBody[\S\s]*\",')
rex_art.findall(story_str000)

['articleBody":"The Senate passed a bill late Thursday evening to suspend the nation’s debt limit through January 1, 2025, averting a first-ever US default just days ahead of the deadline.  The House earlier this week already passed the measure, which can now be sent to President Joe Biden to be signed into law. Biden, just moments after the Senate passed the debt limit bill, praised Congress for its efforts and said in a statement, “I look forward to signing this bill into law as soon as possible.” The president will deliver an address to the nation on Friday on averting default.  Suspending the debt limit through 2025 takes the threat of default off table until after the presidential election. In addition to addressing the debt limit, the bill caps non-defense spending, expands work requirements for some food stamp recipients and claws back some Covid-19 relief funds, among other policy provisions. The Senate voted 63 to 36 to pass the bill. The timeframe to pass the bill through Con

In [9]:
story_str000_bs.find(class_='articleBody')

In [10]:
story_str100 = df['article_text'][100]
print(story_str100)

<!DOCTYPE html>
<html data-layout-uri="cms.cnn.com/_layouts/layout-with-rail/instances/business-article-v1@published" data-uri="cms.cnn.com/_pages/h_4596b35e4178fb5f0515f4be57f0fbc5@published" lang="en">
 <head>
  <style>
   body,h1,h2,h3,h4,h5{font-family:'CNN Sans Display',Helvetica Neue,Helvetica,Arial,Utkal,sans-serif}@font-face{font-family:'CNN Sans Display';src:url(/fonts/cnn/cnnsans.woff) format('woff');font-weight:400;font-display:fallback}@font-face{font-family:'CNN Sans Display';src:url(/fonts/cnn/cnnsans-medium.woff) format('woff');font-weight:500;font-display:fallback}@font-face{font-family:'CNN Sans Display';src:url(/fonts/cnn/cnnsans-bold.woff) format('woff');font-weight:600;font-display:fallback}h1,h2,h3,h4,h5{font-weight:700}:root{--theme-background:#0c0c0c;--theme-divider:#404040;--theme-copy:#404040;--theme-copy-accent:#e6e6e6;--theme-copy-accent-hover:#ffffff;--theme-icon-color:#e6e6e6;--theme-icon-color-hover:#ffffff;--theme-ad-slot-background-color:#0c0c0c;--theme-

In [11]:
rex_art100 = rex.compile(r'articleBody[\S\s]+}')
rex_art100.findall(story_str100)

['articleBody":"Amazon has agreed to pay more than $30 million to settle two federal lawsuits alleging that the tech giant violated users’ privacy — including that of children — through its Alexa voice assistant and its Ring doorbell cameras.  The twin settlements Wednesday with the Federal Trade Commission highlight claims that Amazon retained Ring videos and Alexa voice recordings, along with related geolocation information, for years – in some cases without consent and despite requests by consumers for the data to be deleted.  In addition, the FTC alleged that lax data policies at Amazon meant that the information could often be accessed by unauthorized parties — and often was, in the case of Ring doorbell footage.  “While we disagree with the FTC’s claims regarding both Alexa and Ring, and deny violating the law, these settlements put these matters behind us,” Amazon said in a statement Wednesday. Amazon acquired Ring in 2018, paving the way for the e-commerce giant to get into the

print(df.head())
print(df['article_text'][100])

### Commit changes and close cursor and connection instances

In [12]:
# Commit the changes to the database
db_conn.commit()

# Close the cursor and database connection
cursor.close()
db_conn.close()